# Load Data

In [0]:
from google.colab import drive
drive.mount('/content/drive')

Go to this URL in a browser: https://accounts.google.com/o/oauth2/auth?client_id=947318989803-6bn6qk8qdgf4n4g3pfee6491hc0brc4i.apps.googleusercontent.com&redirect_uri=urn%3Aietf%3Awg%3Aoauth%3A2.0%3Aoob&scope=email%20https%3A%2F%2Fwww.googleapis.com%2Fauth%2Fdocs.test%20https%3A%2F%2Fwww.googleapis.com%2Fauth%2Fdrive%20https%3A%2F%2Fwww.googleapis.com%2Fauth%2Fdrive.photos.readonly%20https%3A%2F%2Fwww.googleapis.com%2Fauth%2Fpeopleapi.readonly&response_type=code

Enter your authorization code:
··········
Mounted at /content/drive


In [0]:
!unzip '/content/drive/My Drive/Colab Notebooks/cv-data.zip'

Archive:  /content/drive/My Drive/Colab Notebooks/cv-data.zip
   creating: 0/
  inflating: 0/.DS_Store             
   creating: __MACOSX/
   creating: __MACOSX/0/
  inflating: __MACOSX/0/._.DS_Store  
  inflating: 0/anger-1.jpg           
  inflating: 0/anger-1000.jpg        
  inflating: 0/anger-1006.jpg        
  inflating: 0/anger-1007.jpg        
  inflating: 0/anger-1009.jpg        
  inflating: 0/anger-1010.jpg        
  inflating: 0/anger-1012.jpg        
  inflating: 0/anger-1013.jpg        
  inflating: 0/anger-1015.jpg        
  inflating: 0/anger-1016.jpg        
  inflating: 0/anger-1022.jpg        
  inflating: 0/anger-1023.jpg        
  inflating: 0/anger-1026.jpg        
  inflating: 0/anger-1028.jpg        
  inflating: 0/anger-103.jpg         
  inflating: 0/anger-1030.jpg        
  inflating: 0/anger-1031.jpg        
  inflating: 0/anger-1032.jpg        
  inflating: 0/anger-1034.jpg        
  inflating: 0/anger-1036.jpg        
  inflating: 0/anger-1037.jpg        


In [0]:
from matplotlib import pyplot as plt 

In [0]:
!cd '/content/drive' 
!ls

0  1  2  3  4  drive  __MACOSX	sample_data


In [0]:
plt.imread('./4/surprise-999.jpg')

array([[[  0, 136, 184],
        [  0, 136, 184],
        [  0, 136, 184],
        ...,
        [168, 152, 152],
        [168, 152, 152],
        [167, 151, 151]],

       [[  0, 136, 184],
        [  0, 136, 184],
        [  0, 136, 184],
        ...,
        [168, 152, 152],
        [168, 152, 152],
        [168, 152, 152]],

       [[  0, 136, 184],
        [  0, 136, 184],
        [  0, 136, 184],
        ...,
        [168, 152, 152],
        [168, 152, 152],
        [168, 152, 152]],

       ...,

       [[129,  98,  80],
        [128,  97,  79],
        [130,  98,  83],
        ...,
        [ 86,  36,   3],
        [ 85,  36,   4],
        [ 85,  36,   6]],

       [[138, 106,  93],
        [136, 104,  91],
        [136, 104,  93],
        ...,
        [ 86,  39,  11],
        [ 85,  41,  14],
        [ 85,  41,  16]],

       [[153, 121, 110],
        [146, 113, 104],
        [139, 109,  99],
        ...,
        [ 88,  42,  16],
        [ 86,  44,  20],
        [ 86,  45,  23]]

if it is zip type, use the following commend:

!tar -zxvf address1 -C address2

!invidia-sml //检测GPU是否连接成功

# Baseline
tools/packages needed:
- face-recognition
- cv2
- PIL
- tensorflow
- keras
- gc
- glob



In [0]:
!pip install face_recognition
!pip install pillow
!pip install glob

     |████████████████████████████████| 100.2MB 33.3MB/s 
  Created wheel for face-recognition-models: filename=face_recognition_models-0.3.0-py2.py3-none-any.whl size=100566176 sha256=f99493df748fb9731f8d8ca583fc762b82143852aa718daa493d471a3049b6a9
  Stored in directory: /root/.cache/pip/wheels/d2/99/18/59c6c8f01e39810415c0e63f5bede7d83dfb0ffc039865465f
Successfully built face-recognition-models
  ERROR: Could not find a version that satisfies the requirement glob (from versions: none)
ERROR: No matching distribution found for glob


## crop the image
things need to do:
- crop the face out
- convert image type 
- zoom in/out (注意等比)
- save the face

In [0]:
import face_recognition
import glob
import cv2 
from PIL import Image 
import os
import pickle
import gc
import numpy as np
import tensorflow as tf

In [0]:
class preprocess(object):
    def __init__(self,scale_size=139):
        self.img_cant = []
        self.scale_size = scale_size

    @staticmethod
    def show_face(path):
        image=face_recognition.load_image_file(path)
        face_locations=face_recognition.face_locations(image)
        if len(face_locations)==0:
            return -1
        for k,i in enumerate(face_locations):
            (a,b,c,d)=i
            image_spilt=image[a:c,d:b,:]
            cv2.imshow('img_{}'.format(k),image_spilt)
            return 1


    def split_face(self,in_path,out_path,use_cnn):
        image=face_recognition.load_image_file(in_path)
        if max(image.shape)>2000:
            if image.shape[0]>image.shape[1]:
                image=cv2.resize(image,(2000,int(2000*image.shape[1]/image.shape[0])))
            else:
                image=cv2.resize(image,(int(2000*image.shape[0]/image.shape[1]),2000))

        if not use_cnn:
            face_locations=face_recognition.face_locations(image)
        else:
            face_locations = face_recognition.face_locations(image, number_of_times_to_upsample=1, model="cnn")
        img_name=os.path.basename(in_path)
        if len(face_locations)==0:
            self.img_cant.append(img_name)
            print(img_name)
            return
        for k,i in enumerate(face_locations):
            (a,b,c,d)=i
            image_spilt=image[a:c,d:b,:]
            image_spilt = self.scale_img(image_spilt)
            img=Image.fromarray(image_spilt)
            img.save(out_path+'/{}_{}.png'.format(img_name,k))
            print('success')

    def scale_img(self,img):
        h, w = img.shape[:2]
        if h > w:
            new_h, new_w = self.scale_size * h / w, self.scale_size
        else:
            new_h, new_w = self.scale_size, self.scale_size * w / h
        
        new_h, new_w = int(new_h), int(new_w)
        img = cv2.resize(img, (new_w, new_h))
        
        if h == w:
            return img 
        elif h<w:
          top = 0
          if new_w <= self.scale_size:
            left = 0
          else:
            left = np.random.randint(0, new_w - self.scale_size)
        elif h>w:
          left = 0
          if new_h <= self.scale_size:
            top = 0
          else:
            top = np.random.randint(0, new_h - self.scale_size)
            

        img = img[top: top + self.scale_size,
                  left: left + self.scale_size]
        return img

    def preprocess(self,in_path,out_path,use_cnn=False):
        path_lst=glob.glob(in_path+'/*.jpg')
        for index,path in enumerate(path_lst):
            if index % 20==0:
                gc.collect()
            print(path)
            self.split_face(path,out_path,use_cnn)

In [10]:
dir_list = ['/content/{}'.format(i) for i in range(5)]
train_ins = preprocess()
for in_path in dir_list:
  out_path = os.path.basename(in_path)+'_face'
  if not os.path.exists(out_path):
    os.mkdir(out_path)
  train_ins.preprocess(in_path,out_path,use_cnn=False)
  with open('train_face_cant_{}.pkl'.format(os.path.basename(in_path)),'wb')as f:
    pickle.dump(train_ins.img_cant,f)
    

/content/0/anger-580.jpg
success
/content/0/anger-219.jpg
success
/content/0/anger-357.jpg
success
/content/0/anger-686.jpg
success
/content/0/anger-880.jpg
success
/content/0/anger-789.jpg
success
/content/0/anger-663.jpg
success
/content/0/anger-961.jpg
success
/content/0/anger-742.jpg
success
/content/0/anger-867.jpg
success
/content/0/anger-1190.jpg
success
/content/0/anger-658.jpg
success
/content/0/anger-73.jpg
success
/content/0/anger-781.jpg
success
/content/0/anger-840.jpg
success
/content/0/anger-1205.jpg
success
/content/0/anger-285.jpg
success
/content/0/anger-106.jpg
success
/content/0/anger-496.jpg
success
success
/content/0/anger-1141.jpg
success
/content/0/anger-1090.jpg
anger-1090.jpg
/content/0/anger-217.jpg
success
/content/0/anger-283.jpg
success
/content/0/anger-735.jpg
success
/content/0/anger-897.jpg
success
/content/0/anger-15.jpg
success
/content/0/anger-694.jpg
success
/content/0/anger-854.jpg
success
/content/0/anger-1046.jpg
success
/content/0/anger-1186.jpg

 # Create tfrecord

In [0]:
#图像标签生成tfrecord函数
import tensorflow as tf
import numpy as np
import os
from tqdm import tqdm
from PIL import Image
import numpy as np
import sys
def image2tfrecord(image_list,label_list,filename):
    '''
    image_list:image path list
    label_list:label list
    '''
    length=len(image_list)
    writer=tf.python_io.TFRecordWriter(filename)
    for i in range(length):
        if i % 100==0:
            ratio=round(i/float(length),4)
            sys.stdout.write('ratio:{}\r'.format(ratio))
            sys.stdout.flush()
        image=Image.open(image_list[i])
        if 'png' in image_list[i][-4:]:
            if image.mode=='RGB':
                r, g, b = image.split()
                image = Image.merge("RGB", (r, g, b))
            elif image.mode=='L':
                pass
            else:
                r,g, b, a = image.split()
                image = Image.merge("RGB", (r, g, b))
        image=image.resize((139,139))
        #这个地方就展开了
        image_bytes=image.tobytes()
        features={}
        features['image']=tf.train.Feature(bytes_list=tf.train.BytesList(value=[image_bytes]))
        features['label']=tf.train.Feature(int64_list=tf.train.Int64List(value=[int(label_list[i])]))
        tf_features=tf.train.Features(feature=features)
        tf_example=tf.train.Example(features=tf_features)
        tf_serialized=tf_example.SerializeToString()
        writer.write(tf_serialized)
    writer.close()

In [20]:
cwd = os.path.join(os.getcwd())
print(cwd)
# create 10 tfrecords
# divide for training set and test set
random_ratio = 0.05
sum_number = 0
for i in range(5):
    print(i)
    image_list = np.array(glob.glob(os.path.join(cwd,'{}_face'.format(i))+'/*.png'))
    test_choice = np.random.choice(range(len(image_list)),size=int(len(image_list)*random_ratio))
    train_choice = list(set(range(len(image_list))).difference(test_choice))
    image_list_train = image_list[train_choice]
    image_list_test = image_list[test_choice]
    label_list = np.zeros(len(image_list))+i
    image2tfrecord(image_list_train,np.zeros(len(image_list_train))+i,'face_train_{}.tfrecords'.format(i))
    image2tfrecord(image_list_test,np.zeros(len(image_list_test))+i,'face_test_{}.tfrecords'.format(i))

/content
0
1
2
3
4


In [0]:
#解析函数
def pares_tf(example_proto):
    dics={}
    dics['label']=tf.FixedLenFeature((),dtype=tf.int64,default_value=0)
    dics['image']=tf.FixedLenFeature((),dtype=tf.string,default_value="")

    parsed_example=tf.parse_single_example(serialized=example_proto,features=dics)
    image=tf.decode_raw(parsed_example['image'],out_type=tf.uint8)
    #image=tf.image.decode_jpeg(parsed_example['image'], channels=1)
    
    image=tf.reshape(image,(139,139,3))
    image=pre_process(image) # data augmentation
    image=tf.cast(image,tf.float32)/255  #data normalization 归一化
    #标签的操作
    label=parsed_example['label']
    label=tf.cast(label,tf.int32)
    label = tf.one_hot(label,depth=5,on_value=1.0,off_value=0.0)
    return image,label

In [0]:
#dataset
def dataset(filenames,batch_size,epochs):
    dataset=tf.data.TFRecordDataset(filenames=filenames)
    new_dataset=dataset.map(pares_tf)
    shuffle_dataset=new_dataset.shuffle(buffer_size=(100000))
    batch_dataset=shuffle_dataset.batch(batch_size).repeat(epochs)
    batch_dataset=batch_dataset.prefetch(1)
    iterator=batch_dataset.make_one_shot_iterator()
    next_element=iterator.get_next()
    return next_element

In [0]:
# Data proprocess
def pre_process(images,random_flip_up_down=False,random_flip_left_right=False,random_brightness=True,random_contrast=True,random_saturation=False,random_hue=False):
    if random_flip_up_down:
        images = tf.image.random_flip_up_down(images)
    if random_flip_left_right:
        images = tf.image.random_flip_left_right(images)
    if random_brightness:
        images = tf.image.random_brightness(images, max_delta=0.2)
    if random_contrast:
        images = tf.image.random_contrast(images, 0.9, 1.1)
    if random_saturation:
        images = tf.image.random_saturation(images, 0.3, 0.5)
    if random_hue:
        images = tf.image.random_hue(images,0.2)
    new_size = tf.constant([139,139],dtype=tf.int32)
    images = tf.image.resize_images(images, new_size)
    return images

In [0]:
tf.reset_default_graph()
filenames=['face_train_{}.tfrecords'.format(i) for i in range(5)]
next_element=dataset(filenames,batch_size=5,epochs=1)
init = tf.global_variables_initializer()

In [34]:
with tf.Session() as sess:
    sess.run(init)
    batch_images,batch_labels=sess.run([next_element[0],next_element[1]])
    for i in range(batch_images.shape[0]):
        print(batch_images[i].shape)
        img = np.array(batch_images[i])

(139, 139, 3)
(139, 139, 3)
(139, 139, 3)
(139, 139, 3)
(139, 139, 3)


# Create Model

In [37]:
import tensorflow as tf
import sys
import glob

tf.reset_default_graph()
epochs = 15
batch_size = 32
total_sum = 0
epoch = 0
random_ratio = 0.05

filenames_train=['face_train_{}.tfrecords'.format(i) for i in range(5)]
filenames_test=['face_test_{}.tfrecords'.format(i) for i in range(5)]

test_num = sum([int(len(glob.glob('./{}_face/*.png'.format(i)))*random_ratio) for i in range(5)])
train_num = sum([len(glob.glob('./{}_face/*.png'.format(i))) for i in range(5)])-test_num

next_element_train=dataset(filenames_train,batch_size=batch_size,epochs=epochs)
next_element_trest=dataset(filenames_test,batch_size=batch_size,epochs=1)

#two placeholders

input_data = tf.placeholder(tf.float32,shape=(None,139,139,3))
input_label = tf.placeholder(tf.float32,shape=(None,5))


#139
hidden = tf.keras.layers.Conv2D(filters=16,kernel_size=3,strides=1,padding='valid',activation='relu')(input_data)
#137
hidden = tf.keras.layers.MaxPool2D(pool_size=2)(hidden)
#68
hidden = tf.keras.layers.Conv2D(filters=32,kernel_size=3,strides=2,padding='same',activation='relu')(hidden)
#34
hidden = tf.keras.layers.MaxPool2D(pool_size=2)(hidden)
#17
# (17+0(padding)-3 )/2 +1
hidden = tf.keras.layers.Conv2D(filters=64,kernel_size=3,strides=2,padding='valid',activation='relu')(hidden)
#8
hidden = tf.keras.layers.MaxPool2D(pool_size=2)(hidden)
#4
#(4-3+2*0 )/2 (floor int) +1
hidden = tf.keras.layers.Conv2D(filters=128,kernel_size=3,strides=2,padding='valid',activation='relu')(hidden)
#1
# 1x1x128 need to flat it
hidden = tf.layers.Flatten()(hidden)

output = tf.keras.layers.Dense(5,activation='softmax')(hidden)

# loss function

loss = tf.reduce_mean(tf.keras.losses.categorical_crossentropy(input_label,output))

#optimizer
opt = tf.train.AdamOptimizer()
train_op = opt.minimize(loss)

# 测试评估
acc = tf.reduce_mean(tf.keras.metrics.categorical_accuracy(input_label,output))
#correct_pred = tf.equal(tf.argmax(input_label,axis=1),tf.argmax(output,axis=1))
#acc = tf.reduce_mean(tf.cast(correct_pred,tf.float32))

tf.add_to_collection('my_op',input_data)
tf.add_to_collection('my_op',output)
tf.add_to_collection('my_op',loss)

init = tf.global_variables_initializer()
saver = tf.train.Saver()


with tf.Session() as sess:
    sess.run([init])
    while epoch<epochs:
        data,label=sess.run([next_element_train[0],next_element_train[1]])
        total_sum+=batch_size
        _,loss_val = sess.run([train_op,loss],feed_dict={input_data:data,input_label:label})
        if total_sum%20==0: #print for each 20 
            sys.stdout.write('epoch:{},index:{}\\{},loss:{:.4f}\r'.format(epoch,total_sum%train_num,train_num,loss_val))
            sys.stdout.flush()
        if total_sum//train_num>epoch:
            epoch = total_sum//train_num
            loss_val = sess.run([loss],feed_dict={input_data:data,input_label:label})
            
            #calculate the loss for the test set
            #when the dataset is very large, even the loss is large. we could save the 1/20 of the result to reduce the memory needed.
            next_element_test=dataset(filenames_test,batch_size=batch_size,epochs=1)
            total_test_sum = 0
            acc_test_lst = []
            while total_test_sum<test_num:
                total_test_sum+=batch_size
                test_data,test_label=sess.run([next_element_test[0],next_element_test[1]])
                acc_test = sess.run([acc],feed_dict={input_data:test_data,input_label:test_label})
                acc_test_lst.append(acc_test[0])
            acc_val = sum(acc_test_lst)/len(acc_test_lst)
            saver.save(sess, save_path="./model/my_model.ckpt")
            print('epoch:{},train_loss:{:.4f},test_acc:{:.4f}'.format(epoch,loss_val[0],acc_val))

epoch:1,train_loss:0.9431,test_acc:0.7106
epoch:2,train_loss:0.5502,test_acc:0.7474
epoch:3,train_loss:0.8990,test_acc:0.7427
epoch:4,train_loss:0.5142,test_acc:0.7573
epoch:5,train_loss:0.5603,test_acc:0.7708
epoch:6,train_loss:0.5817,test_acc:0.7778
epoch:7,train_loss:0.4543,test_acc:0.7778
epoch:8,train_loss:0.4186,test_acc:0.7932
epoch:9,train_loss:0.3551,test_acc:0.7955
epoch:10,train_loss:0.3423,test_acc:0.8003
epoch:11,train_loss:0.3367,test_acc:0.7882
epoch:12,train_loss:0.4292,test_acc:0.7867
epoch:13,train_loss:0.3531,test_acc:0.8003
epoch:14,train_loss:0.5044,test_acc:0.7900
epoch:15,train_loss:0.2931,test_acc:0.7869
